In [1]:
# 標準ライブラリ
import sys
from pathlib import Path
from typing import Any, Callable, Dict, List, Tuple

# サードパーティのライブラリ
import lightgbm as lgb
import numpy as np
import pandas as pd
from IPython.display import HTML

# ローカルのライブラリ
sys.path.append("../")
from CPoC import *

# マークダウンの体裁
HTML(f'<link rel="stylesheet" type="text/css" href="md.css">')

<head>
    <script type="text/javascript" async
        src="https://cdnjs.cloudflare.com/ajax/libs/mathjax/2.7.5/MathJax.js?config=MML_SVG"></script>
    <link rel="stylesheet" href="md.css">
</head>

<body>
    <h2>評価関数を設計する</h2>
    <!-- 前提のフィールドセット -->
    <fieldset class="fieldset-container" style="margin-bottom: 2em;">
        <legend class="fieldset-title">
            前提
        </legend>
        <ul class="list-items">
            <li>顧客は、町中華の経営者Aさん。</li>
            <li>毎週日曜日、ひいきの農家から一週間分の食材を取り寄せている。</li>
            <li>鮮度を大事にするAさんは、保管して一週間が経過した食材<br>
             ―― 次の日曜日が来た時点で使わずに残った食材 ―― を捨てる。</li>
            <li>捨てる食材を減らすため、お客さんをどんどん受け入れて、<br>
            積極的に食材を使えばいいというわけでもない。<br>
            金曜日・土曜日に予約してくれたお客さんに、<br>食材を取っておく必要があるからだ。</li>
        </ul>
    </fieldset>
    <!-- 問題設定のフィールドセット -->
    <fieldset class="fieldset-container">
        <legend class="fieldset-title">
            問題設定
        </legend>
        <ul class="list-items">
            <li>Aさんは、<span>週次利益が最大になるように</span>、食材を取り寄せたい。</li>
            <li>次のように、週次利益をチャンクダウンして、定式化した。
            </li>
            <p>週次利益 = <span>売上</span> - 費用</p>
            <p>週次利益 = 客単価 * 来店客数 - <span>費用</span></p>
            <p>週次利益 = 客単価 * 来店客数 - (固定費 + <span>食材費</span>)</p>
            <p>週次利益 = 客単価 * 来店客数 - (固定費 + 一人あたりの原価 × 来店客数)</p>
            <li>毎週日曜日に、次の一週間の来店客数を考慮して、食材を取り寄せる。<br>
            つまり、食材費の計算に使う来店客数は、<span>予測値</span>。
            </li>
            <li>来店客数が予測を上回ると、食材を使いすぎないように、<br>
            その日はお店を閉めることにしている。<br>
            つまり、売上の計算に使う来店客数は、<br>
            <span>来店客数の実現値と予測値を比べて、小さい方</span>。<br>
            予測値以上の来店客数になることはないからだ。
            </li>
        </ul>
    </fieldset>
    <!-- 評価関数のフィールドセット -->
    <fieldset class="fieldset-container">
        <legend class="fieldset-title">
            評価関数
        </legend>
        <ul class="list-items">
            <li>固定費は定数なので、考える必要はない。</li>
            <li>基礎集計から、以下のことが判明している。</li>
            <p>客単価: 5,000円</p>
            <p>一人あたりの原価: 2,000円</p>
            <li>最大化したい評価関数を以下のように設定した。</li>
            <p>週次利益 = 5,000 * min(来店客数(実現値), 来店客数(予測値))<br>- 2,000 * 来店客数(予測値)
        </ul>
    </fieldset>
</body>

In [2]:
# 宣言: 客単価と一人あたりの原価
price_per_customer: int = 5000
cost_per_customer: int = 2000

# 宣言: カスタム評価関数
def make_eval_func() -> Callable:
    """
    カスタム評価関数をつくるエンクロージャ\n
    ※ lightGBM 用

    Returns
    -------
    Callable
        カスタム評価関数
    """
    def eval_func(
        preds: np.ndarray,
        data: lgb.Dataset,
    ) -> Tuple[str, float, bool]:
        y = data.get_label()
        
        # 一日当たりの利益
        gain_per_day = price_per_customer * np.minimum(preds, y) - cost_per_customer * preds
        min_arr = np.minimum(preds, y)
        print("---------------------------")
        print(preds[:6])
        print(y[:6])
        print(min_arr[:6])
        print("---------------------------")
        
        # 総利益
        gain = np.sum(gain_per_day)
        
        return "gain", gain, True
    
    return eval_func

In [3]:
# 宣言: バンチの名前
bunch_name: str = "trial"

# 宣言: タスクの種類
task: str = "regression"

# 宣言: 目的変数
target: str = "visitors"

# 宣言: 特徴量
features: List[str] = [
    "is_Monday",
    "is_Tuesday",
    "is_Wednesday",
    "is_Thursday",
    "is_Friday",
    "is_Saturday",
    "is_Sunday",
    "is_holiday",
    "visitors_last_week",
    "visitors_2_week_ago",
    "visitors_3_week_ago",
    "visitors_4_week_ago",
]

# 宣言: モデルのレシピ
recipes: List[Dict[str, Any]] = [
    {
        "model_class": ModelLGB,
        "model_name": "lgb1",
        "fixed_params": {"objective": "regression", "early_stopping_rounds": 10},
        "make_eval_func": make_eval_func,
    },
    # {
    #     "model_class": ModelLGB,
    #     "model_name": "lgb3",
    #     "fixed_params": {"objective": "regression", "early_stopping_rounds": 10},
    #     "make_eval_func": make_eval_func,
    # },
]

# 宣言: 損失関数や評価関数に必要なカラム
# additions: List[str] = [] #["visit_date"]

# 処理: 各パラメータの妥当性を確認
var: Validator = Validator(bunch_name, task, target, features, recipes)
var.check_attributes()

Instance validated successfully. It is safe to pass this instance to the Trainer's constructor.


In [4]:
# 処理: 交差検証
tr = Trainer(var)
tr.train_cv()

2023-06-16 20:13:28,639 - general - INFO - [2023-06-16 20:13:28] - trial - start training cv
2023-06-16 20:13:28,640 - general - INFO - [2023-06-16 20:13:28] - trial fold 0 - start training
[I 2023-06-16 20:13:28,646] A new study created in memory with name: no-name-a94ec8fa-bc56-42ba-8d44-d3c9f78c748d
[I 2023-06-16 20:13:28,760] Trial 0 finished with value: 678.006602280787 and parameters: {'max_depth': 38, 'min_data_in_leaf': 27, 'feature_fraction': 0.8126139487278388, 'bagging_fraction': 0.47410376010807737, 'learning_rate': 0.01628609868764589, 'lambda_l1': 4.65930784235902, 'lambda_l2': 7.578472327493115, 'min_gain_to_split': 0.6686568113859626, 'num_boost_round': 337, 'max_bin': 428}. Best is trial 0 with value: 678.006602280787.
[I 2023-06-16 20:13:28,776] Trial 1 finished with value: 742.2860775588049 and parameters: {'max_depth': 9, 'min_data_in_leaf': 192, 'feature_fraction': 0.8136469194881799, 'bagging_fraction': 0.7011700976202948, 'learning_rate': 0.07264600902376679, 'la

[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000097 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 275
[LightGBM] [Info] Number of data points in the train set: 308, number of used features: 11
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Info] Start training from score 41.636364
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
---------------------------
[41.69963548 41.69963548 41.57961949 41.7744384  41.69963548 41.7744384 ]
[47. 41. 26. 45. 35. 81.]
[41.69963548 41.         26.         41.7744384  35.         41.

[I 2023-06-16 20:13:29,089] Trial 3 finished with value: 676.0816409115432 and parameters: {'max_depth': 21, 'min_data_in_leaf': 20, 'feature_fraction': 0.8768190172650682, 'bagging_fraction': 0.9617340035661007, 'learning_rate': 0.006068887588018143, 'lambda_l1': 7.275604875562629, 'lambda_l2': 4.106115603464408, 'min_gain_to_split': 0.3931977329319641, 'num_boost_round': 406, 'max_bin': 441}. Best is trial 3 with value: 676.0816409115432.
[I 2023-06-16 20:13:29,114] Trial 4 finished with value: 742.2860775588049 and parameters: {'max_depth': 28, 'min_data_in_leaf': 176, 'feature_fraction': 0.9338778146333713, 'bagging_fraction': 0.9211604310479117, 'learning_rate': 0.008509055221518805, 'lambda_l1': 5.777542410565941, 'lambda_l2': 5.606147595325242, 'min_gain_to_split': 0.658520942994589, 'num_boost_round': 167, 'max_bin': 274}. Best is trial 3 with value: 676.0816409115432.
[I 2023-06-16 20:13:29,161] Trial 5 finished with value: 679.3979875164272 and parameters: {'max_depth': 13, '

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
---------------------------
[38.63571191 37.06433867 34.46712305 41.0254981  44.88391012 44.85152322]
[47. 41. 26. 45. 35. 81.]
[38.63571191 37.06433867 26.         41.0254981  35.         44.85152322]
---------------------------
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
---------------------------
[38.587501   37.04869639 34.45148076 41.01782888 44.8356992  44.85029213]
[47. 41. 26. 45. 35. 81.]
[38.587501   37.04869639 26.         41.01782888 35.         44.85029213]
---------------------------
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
---------------------------
[38.5629396  37.01526345 34.43713324 40.98439594 44.86981132 44.82573074]
[47. 41. 26. 45. 35. 81.]
[38.5629396  37.01526345 26.         40.98439594 35.         44.82573074]
---------------------------
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
----------

[I 2023-06-16 20:13:29,248] Trial 9 finished with value: 742.1641480323808 and parameters: {'max_depth': 42, 'min_data_in_leaf': 105, 'feature_fraction': 0.8999924085339462, 'bagging_fraction': 0.6541098806442409, 'learning_rate': 0.03216826641370397, 'lambda_l1': 6.264140005274875, 'lambda_l2': 7.966085324525256, 'min_gain_to_split': 0.7771269099188054, 'num_boost_round': 632, 'max_bin': 256}. Best is trial 3 with value: 676.0816409115432.
[I 2023-06-16 20:13:29,363] Trial 10 finished with value: 739.8476061219527 and parameters: {'max_depth': 19, 'min_data_in_leaf': 64, 'feature_fraction': 0.9791078538496345, 'bagging_fraction': 0.9920174938532269, 'learning_rate': 0.003925502237906228, 'lambda_l1': 9.971625954463171, 'lambda_l2': 0.47906792369462003, 'min_gain_to_split': 0.41118300752747816, 'num_boost_round': 969, 'max_bin': 491}. Best is trial 3 with value: 676.0816409115432.


...

[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.006128 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 249
[LightGBM] [Info] Number of data points in the train set: 309, number of used features: 4
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Info] Start training from score 42.385113
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
---------------------------
[42.22175103 42.4345584  42.22175103 42.35051688 42.4345584  42.22175103]
[21. 53. 38.  9. 27. 66.]
[21.         42.4345584  38.          9.         27.         42.22175103]
---------------------------
Training until validation scores don't improve for 10 rounds
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
---------------------------
[42.16673504 42.50626476 42.08971072 42.21847658 42.5062647

[I 2023-06-16 20:14:04,799] Trial 48 finished with value: 534.002882230591 and parameters: {'max_depth': 39, 'min_data_in_leaf': 39, 'feature_fraction': 0.772758999382701, 'bagging_fraction': 0.47045859771008924, 'learning_rate': 0.028398702876341837, 'lambda_l1': 6.043788984328232, 'lambda_l2': 6.438014074237948, 'min_gain_to_split': 0.43881104512881625, 'num_boost_round': 770, 'max_bin': 444}. Best is trial 39 with value: 529.1788460503204.


---------------------------
[38.34224162 40.16084702 37.07208312 39.06308121 40.53377134 36.3443796 ]
[21. 53. 38.  9. 27. 66.]
[21.         40.16084702 37.07208312  9.         27.         36.3443796 ]
---------------------------
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
---------------------------
[38.20681738 40.02542277 36.84447561 38.83547369 40.3983471  36.11677208]
[21. 53. 38.  9. 27. 66.]
[21.         40.02542277 36.84447561  9.         27.         36.11677208]
---------------------------
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
---------------------------
[38.26054532 39.90398486 36.76663339 38.71403578 40.45207504 35.92521482]
[21. 53. 38.  9. 27. 66.]
[21.         39.90398486 36.76663339  9.         27.         35.92521482]
---------------------------
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
---------------------------
[38.31291555 39.78559514 36.69071392 38.59564606 40.50444

[I 2023-06-16 20:14:04,983] Trial 49 finished with value: 556.542491661485 and parameters: {'max_depth': 48, 'min_data_in_leaf': 47, 'feature_fraction': 0.7941002554415827, 'bagging_fraction': 0.5124237181270718, 'learning_rate': 0.01572148497961246, 'lambda_l1': 7.43094250465176, 'lambda_l2': 6.763538885827832, 'min_gain_to_split': 0.39126879176906443, 'num_boost_round': 878, 'max_bin': 403}. Best is trial 39 with value: 529.1788460503204.
2023-06-16 20:14:05,112 - result - INFO - lgb1_4	552.5279977413032	529.1788460503204
2023-06-16 20:14:05,114 - general - INFO - [2023-06-16 20:14:05] - trial fold 4 - end training
2023-06-16 20:14:05,115 - general - INFO - [2023-06-16 20:14:05] - trial - end training cv


[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000116 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 263
[LightGBM] [Info] Number of data points in the train set: 309, number of used features: 11
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Info] Start training from score 42.385113
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
---------------------------
[42.20585954 42.20585954 42.095702   42.095702   42.44387038 42.32812346]
[21. 53. 38.  9. 27. 66.]
[21.         42.20585954 38.          9.         27.         42.

In [ ]:

# 学習データとテストデータに分割
Splitter.split_data_time_based(
    path=Path("../input") / "data.pkl",
    bunch_name="trial",
    timestamp_col="visit_date",
    test_size=0.1,
)

In [ ]:
# 宣言: 忘却率, 基準日
r = 0.9999
latest_date = pd.Timestamp("2018-06-10")


def make_loss_func1(
    is_for_optuna: bool,
    df: pd.DataFrame,
) -> Callable:
    """
    最新の日付に大きな重みを課す損失関数の例\n
    ※ lightGBM 用

    Parameters
    ----------
    is_for_optuna : bool
        True : Optuna でハイパーパラメータを探索するための損失関数\n
        False : モデルが学習するための損失関数

    df : pd.DataFrame
        カスタム損失関数を生成するために必要なデータフレーム

    Returns
    -------
    Callable
        損失関数
    """
    days_diff = (latest_date - df["visit_date"]).dt.total_seconds() / (24 * 60 * 60)
    weight = r**days_diff
    weight_sum = weight.sum()

    if is_for_optuna:

        def loss_func(
            preds: np.ndarray,
            y: np.ndarray,
        ) -> float:
            val = (weight * (preds - y) ** 2).sum() / weight_sum
            return val

    else:

        def loss_func(
            preds: np.ndarray,
            train_data: lgb.Dataset,
        ) -> Tuple[np.ndarray, np.ndarray]:
            y = train_data.get_label()
            grad = weight * (preds - y)
            hess = weight
            return grad, hess

    return loss_func

In [ ]:
#
bunch_name = "trial"
task = "regression"
target = "visitors"
features = [
    "is_Monday",
    "is_Tuesday",
    "is_Wednesday",
    "is_Thursday",
    "is_Friday",
    "is_Saturday",
    "is_Sunday",
    "is_holiday",
    "visitors_last_week",
    "is_holiday_last_week",
    "visitors_2_week_ago",
    "is_holiday_2_week_ago",
    "visitors_3_week_ago",
    "is_holiday_3_week_ago",
    "visitors_4_week_ago",
    "is_holiday_4_week_ago",
]
recipes = [
    {
        "model_class": ModelLGB,
        "model_name": "lgb1",
        "fixed_params": {"objective": "regression", "metric": "rmse"}
    },
    {
        "model_class": ModelLGB,
        "model_name": "lgb2",
        "fixed_params": {"objective": "regression_l1", "metric": "mae"}
    },
    {
        "model_class": ModelLGB,
        "model_name": "lgb3",
        "fixed_params": {"objective": "regression"},
        "make_eval_func": make_eval_func,
    },
    {
        "model_class": ModelLGB,
        "model_name": "lgb4",
        "fixed_params": {"objective": "regression_l1"},
        "make_eval_func": make_eval_func,
    },
]
additions = ["visit_date"]

var = Validator(bunch_name, task, target, features, recipes, additions)
var.check_attributes()

In [ ]:
var

In [ ]:
rn = Runner(var)
rn.run_train_cv()

In [ ]:
# air_visit_data.csv を pandas の DataFrame の形式で読み込む
air_visit = pd.read_csv(os.path.join(PATH_DATA, "air_visit_data.csv"))

# 店舗ごとに総来店客数を算出
visitor_counts_by_store = (
    air_visit.groupby("air_store_id")["visitors"].sum().reset_index()
)

# 総来店客数が多い上位５店舗だけ表示
visitor_counts_by_store.sort_values("visitors", ascending=False).reset_index(
    drop=True
).head(5)

In [ ]:
from workalendar.asia import Japan

# 　店舗 air_399904bdb7685ca0 の日ごとの来店客数を全量格納
air_visit_max = air_visit.query('air_store_id == "air_399904bdb7685ca0"').reset_index(
    drop=True
)

air_visit_max["visit_date"] = pd.to_datetime(air_visit_max["visit_date"])

air_visit_max["is"] = air_visit_max["visit_date"].dt.dayofweek

# 必要に応じて0-6の整数を文字列の曜日に変換
days = {
    0: "Monday",
    1: "Tuesday",
    2: "Wednesday",
    3: "Thursday",
    4: "Friday",
    5: "Saturday",
    6: "Sunday",
}
air_visit_max["is"] = air_visit_max["is"].apply(lambda x: days[x])

cal = Japan()

# 'day_of_week'カラムが休日であるかどうかを示す新しいカラムを作成
air_visit_max["is_holiday"] = air_visit_max["visit_date"].apply(
    lambda x: int(cal.is_holiday(x))
)

air_visit_max = pd.get_dummies(air_visit_max, columns=["is"])

air_visit_max["visitors_last_week"] = air_visit_max["visitors"].shift(7)
air_visit_max["is_holiday_last_week"] = air_visit_max["is_holiday"].shift(7)
air_visit_max["visitors_2_week_ago"] = air_visit_max["visitors"].shift(14)
air_visit_max["is_holiday_2_week_ago"] = air_visit_max["is_holiday"].shift(14)
air_visit_max["visitors_3_week_ago"] = air_visit_max["visitors"].shift(21)
air_visit_max["is_holiday_3_week_ago"] = air_visit_max["is_holiday"].shift(21)
air_visit_max["visitors_4_week_ago"] = air_visit_max["visitors"].shift(28)
air_visit_max["is_holiday_4_week_ago"] = air_visit_max["is_holiday"].shift(28)
air_visit_max.head(50)

column_order = [
    "visit_date",
    "visitors",
    "is_Monday",
    "is_Tuesday",
    "is_Wednesday",
    "is_Thursday",
    "is_Friday",
    "is_Saturday",
    "is_Sunday",
    "is_holiday",
    "visitors_last_week",
    "is_holiday_last_week",
    "visitors_2_week_ago",
    "is_holiday_2_week_ago",
    "visitors_3_week_ago",
    "is_holiday_3_week_ago",
    "visitors_4_week_ago",
    "is_holiday_4_week_ago",
]
df = air_visit_max[column_order]

# df.head(30)
df = df[df["visit_date"] > "2016-02-01"]

df.to_pickle(os.path.join(PATH_DATA, "data.pkl"))

In [ ]:
dff = pd.read_pickle(os.path.join(PATH_DATA, "data.pkl"))
dff

In [ ]:
from typing import Any, Callable, Union

def check_param_type(param, name, expected_type):
    if not isinstance(param, expected_type):
        raise TypeError(f"Parameter '{name}' must be of type {expected_type}.")

def enclosure(df: pd.DataFrame):
    def closure(val: float):
        pass
    
    return closure``

        
type = Callable[[pd.DataFrame], Callable]
b
check_param_type(enclosure, "alpha", type)

## 損失関数の設計

In [ ]:
from inspect import signature, Parameter
import lightgbm as lgb
from typing import Tuple


def enclosure(
    df: pd.DataFrame,
) -> Callable[[np.ndarray, lgb.Dataset], Tuple[np.ndarray, np.ndarray]]:
    def closure(
        pred: np.ndarray, train_data: lgb.Dataset
    ) -> Tuple[np.ndarray, np.ndarray]:
        return a, b

    return closure


sig = signature(enclosure)
params = sig.parameters


for param in sig.parameters.values():
    print(f"Parameter: {param.name}, Expected type: {param.annotation}")
    print(f"Expected return type: {sig.return_annotation}")
# if len(params) != 2:
#     raise ValueError(
#         "The custom loss function must have exactly two arguments"
#     )

In [ ]:
# RunnerParams
from typing import Callable
import lightgbm as lgb


def loss_for_LGB_example(
    X: pd.DataFrame,
    time_col: str,
    r: float,
) -> Callable:
    """
    LightGBM の損失関数のエンクロージャ。

    最新日時との差分から、重みを計算する。

    Parameters
    ----------
    X : pd.DataFrame
        データフレーム

    time_col : str
        タイムスタンプのカラム名

    r : float
        忘却率

    Returns
    -------
    Callable
    """
    # 忘却率に基づいた重みを設定する
    df[time_col] = pd.to_datetime(df[time_col])
    latest_time = df[time_col].max()
    df["time_difference"] = latest_time - df[time_col]
    weight = r ** df["time_difference"]

    def loss_func(preds: np.ndarray, train_data: lgb.Dataset):
        """
        LightGBM の損失関数

        Parameters
        ----------
        preds : np.ndarray
            予測値

        train_data : lgb.Dataset
            実測値

        Returns
        -------
        Tuple(np.ndarray, np.ndarray)
        """
        y = train_data.get_label()
        grad = weight * (preds - y)
        hess = weight * np.ones(len(y))

        return grad, hess

    return loss_func

In [ ]:
params_dict = {
    "bunch_name": "first",
    "task": "regression",
    "target": "target",
    "features": list(X.columns),
    "model_recipes": model_recipes,
    "model_classes": [ModelLGB],
    "fixed_params": [{}],
    "make_loss_funcs": [loss_for_LGB],
    "make_eval_funcs": [loss_for_LGB],
    "description": "trial",
}
rp = RunnerParams(**params_dict)

# len([loss_for_LGB])

In [ ]:
DataSplitter.split_data("data.pkl", "first", "regression")

In [ ]:
# xgboostによる学習・予測
rr = Runner(rp)
rr.run_train_cv()
# runner = Runner('xgb1', ModelLGB, features, params_xgb)
# runner.run_train_cv()
# runner.run_predict_cv()
# Submission.create_submission('xgb1')

In [ ]:
params = {
            "n_splits": 5,
            "shuffle": True,
            "random_state": 10,
        }
**params